## Import libraries

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files


!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Libraries imported.


In [2]:
pip install lxml


Note: you may need to restart the kernel to use updated packages.


In [3]:
import lxml

In [4]:
%load_ext sql

In [5]:
import ibm_db

In [6]:
# The code was removed by Watson Studio for sharing.

In [7]:
dsn = (
    "DRIVER={0};"
    "DATABASE={1};"
    "HOSTNAME={2};"
    "PORT={3};"
    "PROTOCOL={4};"
    "UID={5};"
    "PWD={6};").format(dsn_driver, dsn_database, dsn_hostname, dsn_port, dsn_protocol, dsn_uid, dsn_pwd)

try:
    conn = ibm_db.connect(dsn, "", "")
    print ("Connected to database: ", dsn_database, "as user: ", dsn_uid, "on host: ", dsn_hostname)

except:
    print ("Unable to connect: ", ibm_db.conn_errormsg() )


Connected to database:  BLUDB as user:  sdg85717 on host:  dashdb-txn-sbox-yp-dal09-04.services.dal.bluemix.net


In [8]:
import ibm_db_dbi

In [9]:
pconn = ibm_db_dbi.Connection(conn)

In [10]:
selectQuery = "select * from RENT_SANTA_CLARA_COUNTY"


In [11]:
rent_scc = pd.read_sql(selectQuery, pconn)

In [12]:
rent_scc

Neighborhood  Average_Rent
0       Santa Clara          2974
1            Gilroy          2215
2    East Foothills          2358
3       Morgan Hill          2390
4         Alum Rock          2508
5          Campbell          2633
6          San Jose          2790
7            Loyola          2819
8          Milpitas          2853
9         Sunnyvale          3016
10        Los Gatos          3054
11  Los Altos Hills          3060
12        Los Altos          3060
13    Mountain View          3291
14        Palo Alto          3347
15        Cupertino          3492

In [13]:
rent_scc['Neighborhood'] = rent_scc['Neighborhood'].str.upper()

In [14]:
rent_scc

Neighborhood  Average_Rent
0       SANTA CLARA          2974
1            GILROY          2215
2    EAST FOOTHILLS          2358
3       MORGAN HILL          2390
4         ALUM ROCK          2508
5          CAMPBELL          2633
6          SAN JOSE          2790
7            LOYOLA          2819
8          MILPITAS          2853
9         SUNNYVALE          3016
10        LOS GATOS          3054
11  LOS ALTOS HILLS          3060
12        LOS ALTOS          3060
13    MOUNTAIN VIEW          3291
14        PALO ALTO          3347
15        CUPERTINO          3492

In [15]:
rent_scc.shape

(16, 2)

In [16]:
!wget --quiet https://earthworks.stanford.edu/download/file/stanford-ht248yt3124-geojson.json -O cities_bayarea.json
    
print('GeoJSON file downloaded!')

GeoJSON file downloaded!


In [17]:
with open('cities_bayarea.json') as json_data:
    cities_bayarea = json.load(json_data)

In [18]:
cities_santaclara = r'cities_bayarea.json' # geojson file


In [19]:
selectQuery1 = "select ZIP, CITY, LATITUDE, LONGITUDE from GEO_CITY_CENTERS"


In [20]:
citycenter_scc = pd.read_sql(selectQuery1, pconn)

In [21]:
ibm_db.close(conn)

True

In [77]:
citycenter_scc

ZIP           CITY   LATITUDE   LONGITUDE
0   95035       MILPITAS  37.432342 -121.897441
1   94022      LOS ALTOS  37.381406 -122.113581
2   94039  MOUNTAIN VIEW  37.390176 -122.081790
3   95008       CAMPBELL  37.288126 -121.944362
4   94301      PALO ALTO  37.444255 -122.160528
5   95030   MONTE SERENO  37.232756 -121.986074
6   95020         GILROY  37.004815 -121.572442
7   95113       SAN JOSE  37.337845 -121.886027
8   94086      SUNNYVALE  37.371408 -122.036903
9   95037    MORGAN HILL  37.125569 -121.662109
10  95050    SANTA CLARA  37.355531 -121.955573
11  95014      CUPERTINO  37.318313 -122.028747
12  95070       SARATOGA  37.267870 -122.014423

In [23]:
rent_scc.rename(columns={'Neighborhood':'CITY'},inplace=True)

In [24]:
Geo_scc_rental = pd.merge(rent_scc, citycenter_scc, on='CITY')

In [25]:
Geo_scc_rental

CITY  Average_Rent    ZIP   LATITUDE   LONGITUDE
0     SANTA CLARA          2974  95050  37.355531 -121.955573
1          GILROY          2215  95020  37.004815 -121.572442
2     MORGAN HILL          2390  95037  37.125569 -121.662109
3        CAMPBELL          2633  95008  37.288126 -121.944362
4        SAN JOSE          2790  95113  37.337845 -121.886027
5        MILPITAS          2853  95035  37.432342 -121.897441
6       SUNNYVALE          3016  94086  37.371408 -122.036903
7       LOS ALTOS          3060  94022  37.381406 -122.113581
8   MOUNTAIN VIEW          3291  94039  37.390176 -122.081790
9       PALO ALTO          3347  94301  37.444255 -122.160528
10      CUPERTINO          3492  95014  37.318313 -122.028747

In [63]:
map_city_santaclara = folium.Map(location = [37.354107, -121.955238], zoom_start = 12)
map_city_santaclara.choropleth(geo_data=cities_santaclara,
                  data=Geo_scc_rental,
                  columns=['CITY', 'Average_Rent'],
                  key_on='feature.properties.name',
                  fill_color='YlOrRd', 
                  fill_opacity=0.7, 
                  line_opacity=0.2,
                  legend_name='Average rent by city'
)
map_city_santaclara

In [64]:
# instantiate a feature group for the incidents in the dataframe
rental = folium.map.FeatureGroup()

# loop through the 100 crimes and add each to the incidents feature group
for lat, lng, in zip(Geo_scc_rental.LATITUDE, Geo_scc_rental.LONGITUDE):
    rental.add_child(
        folium.features.CircleMarker(
            [lat, lng],
            radius=5, # define how big you want the circle markers to be
            color='blue',
            fill=True,
            fill_color='black',
            fill_opacity=0.6
        )
    )

# add pop-up text to each marker on the map
latitudes = list(Geo_scc_rental.LATITUDE)
longitudes = list(Geo_scc_rental.LONGITUDE)
labels = list(Geo_scc_rental.CITY)

for lat, lng, label in zip(latitudes, longitudes, labels):
    folium.Marker([lat, lng], popup=label).add_to(map_city_santaclara)    
    
# add incidents to map
map_city_santaclara.add_child(rental)

In [28]:
address = 'Santa Clara County, CA'

geolocator = Nominatim(user_agent="scc_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Santa Clara County are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Santa Clara County are 37.2333253, -121.6846349.


## Foursquare Initializing

In [75]:
# The code was removed by Watson Studio for sharing.

In [30]:
Geo_scc_rental.loc[0, 'CITY']

'SANTA CLARA'

In [31]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['CITY', 
                  'CITY Latitude', 
                  'CITY Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now, let's get the top 100 venues that are in Marble Hill within a radius of 1000 meters.

In [32]:
LIMIT = 100

radius = 1000 # define radius

In [33]:
scc_venues = getNearbyVenues(names=Geo_scc_rental['CITY'],
                                   latitudes=Geo_scc_rental['LATITUDE'],
                                   longitudes=Geo_scc_rental['LONGITUDE']
                                  )

SANTA CLARA
GILROY
MORGAN HILL
CAMPBELL
SAN JOSE
MILPITAS
SUNNYVALE
LOS ALTOS
MOUNTAIN VIEW
PALO ALTO
CUPERTINO


In [34]:
print(scc_venues.shape)
scc_venues.head()

(389, 7)


CITY  CITY Latitude  CITY Longitude  \
0  SANTA CLARA      37.355531     -121.955573   
1  SANTA CLARA      37.355531     -121.955573   
2  SANTA CLARA      37.355531     -121.955573   
3  SANTA CLARA      37.355531     -121.955573   
4  SANTA CLARA      37.355531     -121.955573   

                                     Venue  Venue Latitude  Venue Longitude  \
0                                 Kettle'e       37.352102      -121.954609   
1  BEST WESTERN University Inn Santa Clara       37.352545      -121.955239   
2                        Maple Leaf Donuts       37.355301      -121.959146   
3                     Triton Museum of Art       37.355971      -121.955246   
4                              Chick-fil-A       37.352039      -121.958524   

         Venue Category  
0     Indian Restaurant  
1                 Hotel  
2            Donut Shop  
3            Art Museum  
4  Fast Food Restaurant

#### Let's check how many venues were returned for each neighborhood

In [35]:
scc_venues.groupby('CITY').count()

CITY Latitude  CITY Longitude  Venue  Venue Latitude  \
CITY                                                                  
CAMPBELL                  45              45     45              45   
CUPERTINO                 19              19     19              19   
GILROY                    16              16     16              16   
LOS ALTOS                 48              48     48              48   
MILPITAS                  46              46     46              46   
MORGAN HILL                7               7      7               7   
MOUNTAIN VIEW             38              38     38              38   
PALO ALTO                 73              73     73              73   
SAN JOSE                  37              37     37              37   
SANTA CLARA               16              16     16              16   
SUNNYVALE                 44              44     44              44   

               Venue Longitude  Venue Category  
CITY                                            
CAMPBELL                    45              45  
CUPERTINO                   19              19  
GILROY                      16              16  
LOS ALTOS                   48              48  
MILPITAS                    46              46  
MORGAN HILL                  7               7  
MOUNTAIN VIEW               38              38  
PALO ALTO                   73              73  
SAN JOSE                    37              37  
SANTA CLARA                 16              16  
SUNNYVALE                   44              44

#### Let's find out how many unique categories can be curated from all the returned venues

In [36]:
print('There are {} uniques categories.'.format(len(scc_venues['Venue Category'].unique())))

There are 141 uniques categories.


## 3. Analyze Each Neighborhood

In [37]:
# one hot encoding
scc_onehot = pd.get_dummies(scc_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
scc_onehot['CITY'] = scc_venues['CITY'] 

# move neighborhood column to the first column
fixed_columns = [scc_onehot.columns[-1]] + list(scc_onehot.columns[:-1])
scc_onehot = scc_onehot[fixed_columns]

scc_onehot.head()

CITY  ATM  Accessories Store  American Restaurant  Arcade  \
0  SANTA CLARA    0                  0                    0       0   
1  SANTA CLARA    0                  0                    0       0   
2  SANTA CLARA    0                  0                    0       0   
3  SANTA CLARA    0                  0                    0       0   
4  SANTA CLARA    0                  0                    0       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  BBQ Joint  \
0            0           0                    0                 0          0   
1            0           0                    0                 0          0   
2            0           0                    0                 0          0   
3            0           1                    0                 0          0   
4            0           0                    0                 0          0   

   Bagel Shop  Bakery  Bank  Bar  Beer Bar  Beer Garden  Beer Store  \
0           0       0     0    0         0            0           0   
1           0       0     0    0         0            0           0   
2           0       0     0    0         0            0           0   
3           0       0     0    0         0            0           0   
4           0       0     0    0         0            0           0   

   Big Box Store  Bookstore  Boutique  Breakfast Spot  Bubble Tea Shop  \
0              0          0         0               0                0   
1              0          0         0               0                0   
2              0          0         0               0                0   
3              0          0         0               0                0   
4              0          0         0               0                0   

   Burger Joint  Burmese Restaurant  Bus Station  Bus Stop  Café  \
0             0                   0            0         0     0   
1             0                   0            0         0     0   
2             0                   0            0         0     0   
3             0                   0            0         0     0   
4             0                   0            0         0     0   

   Cajun / Creole Restaurant  Candy Store  Caribbean Restaurant  \
0                          0            0                     0   
1                          0            0                     0   
2                          0            0                     0   
3                          0            0                     0   
4                          0            0                     0   

   Chinese Restaurant  Chocolate Shop  Clothing Store  Cocktail Bar  \
0                   0               0               0             0   
1                   0               0               0             0   
2                   0               0               0             0   
3                   0               0               0             0   
4                   0               0               0             0   

   Coffee Shop  Comedy Club  Comic Shop  Concert Hall  Convenience Store  \
0            0            0           0             0                  0   
1            0            0           0             0                  0   
2            0            0           0             0                  0   
3            0            0           0             0                  0   
4            0            0           0             0                  0   

   Cosmetics Shop  Creperie  Deli / Bodega  Design Studio  Dessert Shop  \
0               0         0              0              0             0   
1               0         0              0              0             0   
2               0         0              0              0             0   
3               0         0              0              0             0   
4               0         0              0              0             0   

   Diner  Donut Shop  Dumpling Restaurant  Electronics Store  Farmers Market  \
0  

In [38]:
scc_onehot.shape

(389, 142)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [39]:
scc_grouped = scc_onehot.groupby('CITY').mean().reset_index()
scc_grouped

CITY       ATM  Accessories Store  American Restaurant    Arcade  \
0        CAMPBELL  0.000000           0.000000             0.000000  0.022222   
1       CUPERTINO  0.000000           0.000000             0.000000  0.000000   
2          GILROY  0.000000           0.000000             0.125000  0.000000   
3       LOS ALTOS  0.020833           0.000000             0.041667  0.000000   
4        MILPITAS  0.000000           0.000000             0.000000  0.000000   
5     MORGAN HILL  0.000000           0.000000             0.000000  0.000000   
6   MOUNTAIN VIEW  0.000000           0.000000             0.026316  0.000000   
7       PALO ALTO  0.000000           0.013699             0.041096  0.000000   
8        SAN JOSE  0.000000           0.000000             0.000000  0.000000   
9     SANTA CLARA  0.000000           0.000000             0.000000  0.000000   
10      SUNNYVALE  0.000000           0.000000             0.000000  0.000000   

    Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  BBQ Joint  \
0      0.000000      0.0000             0.000000          0.000000   0.000000   
1      0.000000      0.0000             0.000000          0.000000   0.000000   
2      0.000000      0.0000             0.000000          0.000000   0.000000   
3      0.000000      0.0000             0.000000          0.000000   0.000000   
4      0.000000      0.0000             0.000000          0.021739   0.000000   
5      0.000000      0.0000             0.000000          0.000000   0.000000   
6      0.000000      0.0000             0.000000          0.000000   0.026316   
7      0.000000      0.0000             0.000000          0.000000   0.000000   
8      0.027027      0.0000             0.000000          0.027027   0.000000   
9      0.000000      0.0625             0.000000          0.000000   0.000000   
10     0.000000      0.0000             0.022727          0.000000   0.000000   

    Bagel Shop    Bakery      Bank       Bar  Beer Bar  Beer Garden  \
0     0.000000  0.022222  0.000000  0.000000  0.022222     0.000000   
1     0.000000  0.052632  0.105263  0.000000  0.000000     0.000000   
2     0.000000  0.000000  0.000000  0.062500  0.000000     0.000000   
3     0.020833  0.062500  0.041667  0.000000  0.000000     0.000000   
4     0.021739  0.000000  0.043478  0.000000  0.000000     0.000000   
5     0.000000  0.000000  0.000000  0.000000  0.000000     0.000000   
6     0.000000  0.026316  0.000000  0.000000  0.000000     0.026316   
7     0.000000  0.000000  0.000000  0.013699  0.000000     0.000000   
8     0.000000  0.027027  0.000000  0.027027  0.027027     0.000000   
9     0.000000  0.000000  0.125000  0.000000  0.000000     0.000000   
10    0.000000  0.000000  0.045455  0.000000  0.000000     0.000000   

    Beer Store  Big Box Store  Bookstore  Boutique  Breakfast Spot  \
0     0.000000       0.000000   0.000000  0.022222        0.022222   
1     0.000000       0.000000   0.000000  0.000000        0.000000   
2     0.000000       0.000000   0.062500  0.000000        0.062500   
3     0.000000       0.000000   0.041667  0.000000        0.041667   
4     0.000000       0.000000   0.000000  0.000000        0.021739   
5     0.000000       0.000000   0.000000  0.000000        0.000000   
6     0.026316       0.000000   0.026316  0.026316        0.000000   
7     0.000000       0.000000   0.013699  0.000000        0.000000   
8     0.000000       0.000000   0.000000  0.000000        0.000000   
9     0.000000       0.000000   0.000000  0.000000        0.062500   
10    0.000000       0.022727   0.000000  0.000000        0.000000   

    Bubble Tea Shop  Burger Joint  Burmese Restaurant  Bus Station  Bus Stop  \
0          0.000000      0.022222            0.000000     0.000000  0.022222   
1          0.000000      0.000000            0.000000     0.000000  0.000000   
2          0.000000      0.000000            0.000000     0.062500  0.000000   
3          0.000000      0.000000            0.000000

In [40]:
scc_grouped.shape

(11, 142)

#### Let's print each neighborhood along with the top 5 most common venues

In [41]:
num_top_venues = 5

for hood in scc_grouped['CITY']:
    print("----"+hood+"----")
    temp = scc_grouped[scc_grouped['CITY'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----CAMPBELL----
                venue  freq
0      Sandwich Place  0.07
1  Italian Restaurant  0.07
2  Mexican Restaurant  0.07
3      Ice Cream Shop  0.04
4         Pizza Place  0.04


----CUPERTINO----
                venue  freq
0  Mexican Restaurant  0.11
1                Bank  0.11
2      Massage Studio  0.05
3              Bakery  0.05
4         Coffee Shop  0.05


----GILROY----
                 venue  freq
0                 Café  0.12
1  American Restaurant  0.12
2   Mexican Restaurant  0.12
3            Bookstore  0.06
4             Wine Bar  0.06


----LOS ALTOS----
                venue  freq
0  Mexican Restaurant  0.06
1         Coffee Shop  0.06
2    Sushi Restaurant  0.06
3              Bakery  0.06
4      Breakfast Spot  0.04


----MILPITAS----
                venue  freq
0      Shopping Plaza  0.04
1         Coffee Shop  0.04
2  Mexican Restaurant  0.04
3      Sandwich Place  0.04
4       Grocery Store  0.04


----MORGAN HILL----
                   venue  freq
0       

#### Let's put that into a *pandas* dataframe

In [42]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [43]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['CITY']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
scc_venues_sorted = pd.DataFrame(columns=columns)
scc_venues_sorted['CITY'] = scc_grouped['CITY']

for ind in np.arange(scc_grouped.shape[0]):
    scc_venues_sorted.iloc[ind, 1:] = return_most_common_venues(scc_grouped.iloc[ind, :], num_top_venues)

scc_venues_sorted.head()

CITY 1st Most Common Venue 2nd Most Common Venue  \
0   CAMPBELL        Sandwich Place    Italian Restaurant   
1  CUPERTINO                  Bank    Mexican Restaurant   
2     GILROY   American Restaurant    Mexican Restaurant   
3  LOS ALTOS                Bakery           Coffee Shop   
4   MILPITAS        Shopping Plaza         Grocery Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0    Mexican Restaurant           Pizza Place        Ice Cream Shop   
1           Coffee Shop              Pharmacy    Chinese Restaurant   
2                  Café        Breakfast Spot                   Bar   
3      Sushi Restaurant    Mexican Restaurant           Pizza Place   
4    Mexican Restaurant          Optical Shop        Sandwich Place   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0              Boutique    Frozen Yogurt Shop           Record Shop   
1     Electronics Store        Sandwich Place        Mattress Store   
2              Wine Bar             Bookstore     Indian Restaurant   
3   American Restaurant                  Bank             Bookstore   
4    Chinese Restaurant                  Bank           Coffee Shop   

  9th Most Common Venue 10th Most Common Venue  
0                Arcade                   Park  
1        Massage Studio                    Spa  
2           Coffee Shop            Bus Station  
3        Breakfast Spot       Greek Restaurant  
4    Seafood Restaurant     Salon / Barbershop

In [44]:
scc_venues_sorted

CITY 1st Most Common Venue 2nd Most Common Venue  \
0        CAMPBELL        Sandwich Place    Italian Restaurant   
1       CUPERTINO                  Bank    Mexican Restaurant   
2          GILROY   American Restaurant    Mexican Restaurant   
3       LOS ALTOS                Bakery           Coffee Shop   
4        MILPITAS        Shopping Plaza         Grocery Store   
5     MORGAN HILL        Ice Cream Shop         Grocery Store   
6   MOUNTAIN VIEW           Coffee Shop                  Park   
7       PALO ALTO                  Café        Ice Cream Shop   
8        SAN JOSE        Sandwich Place        Ice Cream Shop   
9     SANTA CLARA  Fast Food Restaurant   Fried Chicken Joint   
10      SUNNYVALE         Grocery Store           Coffee Shop   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0      Mexican Restaurant           Pizza Place        Ice Cream Shop   
1             Coffee Shop              Pharmacy    Chinese Restaurant   
2                    Café        Breakfast Spot                   Bar   
3        Sushi Restaurant    Mexican Restaurant           Pizza Place   
4      Mexican Restaurant          Optical Shop        Sandwich Place   
5       Convenience Store    Chinese Restaurant      Sushi Restaurant   
6             Yoga Studio                  Pool          Optical Shop   
7             Coffee Shop                 Hotel   American Restaurant   
8   Vietnamese Restaurant    Mexican Restaurant           Coffee Shop   
9       Indian Restaurant                  Bank                 Hotel   
10     Chinese Restaurant     Indian Restaurant                   Spa   

   6th Most Common Venue    7th Most Common Venue 8th Most Common Venue  \
0               Boutique       Frozen Yogurt Shop           Record Shop   
1      Electronics Store           Sandwich Place        Mattress Store   
2               Wine Bar                Bookstore     Indian Restaurant   
3    American Restaurant                     Bank             Bookstore   
4     Chinese Restaurant                     Bank           Coffee Shop   
5            Pizza Place    Vietnamese Restaurant  Fast Food Restaurant   
6       Sushi Restaurant  Health & Beauty Service    Salon / Barbershop   
7              Juice Bar     Gym / Fitness Center                   Spa   
8      Convenience Store                      Pub              Pharmacy   
9         Breakfast Spot             Intersection            Art Museum   
10                  Bank         Halal Restaurant   Rental Car Location   

   9th Most Common Venue    10th Most Common Venue  
0                 Arcade                      Park  
1         Massage Studio                       Spa  
2            Coffee Shop               Bus Station  
3         Breakfast Spot          Greek Restaurant  
4     Seafood Restaurant        Salon / Barbershop  
5           Concert Hall                Hobby Shop  
6            Salad Place               Pastry Shop  
7       Greek Restaurant               Pizza Place  
8            Music Store  Mediterranean Restaurant  
9     Italian Restaurant                Food Truck  
10           Shoe Repair       Dumpling Restaurant

In [45]:
scc_venues_rent_sorted = pd.merge(rent_scc, scc_venues_sorted, on='CITY')
scc_venues_rent_sorted

CITY  Average_Rent 1st Most Common Venue 2nd Most Common Venue  \
0     SANTA CLARA          2974  Fast Food Restaurant   Fried Chicken Joint   
1          GILROY          2215   American Restaurant    Mexican Restaurant   
2     MORGAN HILL          2390        Ice Cream Shop         Grocery Store   
3        CAMPBELL          2633        Sandwich Place    Italian Restaurant   
4        SAN JOSE          2790        Sandwich Place        Ice Cream Shop   
5        MILPITAS          2853        Shopping Plaza         Grocery Store   
6       SUNNYVALE          3016         Grocery Store           Coffee Shop   
7       LOS ALTOS          3060                Bakery           Coffee Shop   
8   MOUNTAIN VIEW          3291           Coffee Shop                  Park   
9       PALO ALTO          3347                  Café        Ice Cream Shop   
10      CUPERTINO          3492                  Bank    Mexican Restaurant   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0       Indian Restaurant                  Bank                 Hotel   
1                    Café        Breakfast Spot                   Bar   
2       Convenience Store    Chinese Restaurant      Sushi Restaurant   
3      Mexican Restaurant           Pizza Place        Ice Cream Shop   
4   Vietnamese Restaurant    Mexican Restaurant           Coffee Shop   
5      Mexican Restaurant          Optical Shop        Sandwich Place   
6      Chinese Restaurant     Indian Restaurant                   Spa   
7        Sushi Restaurant    Mexican Restaurant           Pizza Place   
8             Yoga Studio                  Pool          Optical Shop   
9             Coffee Shop                 Hotel   American Restaurant   
10            Coffee Shop              Pharmacy    Chinese Restaurant   

   6th Most Common Venue    7th Most Common Venue 8th Most Common Venue  \
0         Breakfast Spot             Intersection            Art Museum   
1               Wine Bar                Bookstore     Indian Restaurant   
2            Pizza Place    Vietnamese Restaurant  Fast Food Restaurant   
3               Boutique       Frozen Yogurt Shop           Record Shop   
4      Convenience Store                      Pub              Pharmacy   
5     Chinese Restaurant                     Bank           Coffee Shop   
6                   Bank         Halal Restaurant   Rental Car Location   
7    American Restaurant                     Bank             Bookstore   
8       Sushi Restaurant  Health & Beauty Service    Salon / Barbershop   
9              Juice Bar     Gym / Fitness Center                   Spa   
10     Electronics Store           Sandwich Place        Mattress Store   

   9th Most Common Venue    10th Most Common Venue  
0     Italian Restaurant                Food Truck  
1            Coffee Shop               Bus Station  
2           Concert Hall                Hobby Shop  
3                 Arcade                      Park  
4            Music Store  Mediterranean Restaurant  
5     Seafood Restaurant        Salon / Barbershop  
6            Shoe Repair       Dumpling Restaurant  
7         Breakfast Spot          Greek Restaurant  
8            Salad Place               Pastry Shop  
9       Greek Restaurant               Pizza Place  
10        Massage Studio                       Spa

## Cluster Neighborhoods 1


Run *k*-means to cluster the neighborhood into 5 clusters.

In [46]:
# set number of clusters
kclusters2 = 3

scc_grouped_clustering2 = scc_grouped.drop('CITY', 1)

# run k-means clustering
kmeans2 = KMeans(n_clusters=kclusters2, random_state=0).fit(scc_grouped_clustering2)

# check cluster labels generated for each row in the dataframe
kmeans2.labels_[0:10] 

array([2, 2, 2, 2, 2, 0, 2, 2, 2, 1], dtype=int32)

In [47]:
Geo_scc_rental1 = Geo_scc_rental[['CITY', 'ZIP', 'LATITUDE', 'LONGITUDE']]

In [48]:
Geo_scc_rental1.head()

CITY    ZIP   LATITUDE   LONGITUDE
0  SANTA CLARA  95050  37.355531 -121.955573
1       GILROY  95020  37.004815 -121.572442
2  MORGAN HILL  95037  37.125569 -121.662109
3     CAMPBELL  95008  37.288126 -121.944362
4     SAN JOSE  95113  37.337845 -121.886027

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [49]:
# add clustering labels
scc_venues_rent_sorted.insert(0, 'Cluster Labels0', kmeans2.labels_)

scc_merged2 = Geo_scc_rental1

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
scc_merged2 = scc_merged2.join(scc_venues_rent_sorted.set_index('CITY'), on='CITY')

scc_merged2.head() # check the last columns!

CITY    ZIP   LATITUDE   LONGITUDE  Cluster Labels0  Average_Rent  \
0  SANTA CLARA  95050  37.355531 -121.955573                2          2974   
1       GILROY  95020  37.004815 -121.572442                2          2215   
2  MORGAN HILL  95037  37.125569 -121.662109                2          2390   
3     CAMPBELL  95008  37.288126 -121.944362                2          2633   
4     SAN JOSE  95113  37.337845 -121.886027                2          2790   

  1st Most Common Venue 2nd Most Common Venue  3rd Most Common Venue  \
0  Fast Food Restaurant   Fried Chicken Joint      Indian Restaurant   
1   American Restaurant    Mexican Restaurant                   Café   
2        Ice Cream Shop         Grocery Store      Convenience Store   
3        Sandwich Place    Italian Restaurant     Mexican Restaurant   
4        Sandwich Place        Ice Cream Shop  Vietnamese Restaurant   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0                  Bank                 Hotel        Breakfast Spot   
1        Breakfast Spot                   Bar              Wine Bar   
2    Chinese Restaurant      Sushi Restaurant           Pizza Place   
3           Pizza Place        Ice Cream Shop              Boutique   
4    Mexican Restaurant           Coffee Shop     Convenience Store   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0           Intersection            Art Museum    Italian Restaurant   
1              Bookstore     Indian Restaurant           Coffee Shop   
2  Vietnamese Restaurant  Fast Food Restaurant          Concert Hall   
3     Frozen Yogurt Shop           Record Shop                Arcade   
4                    Pub              Pharmacy           Music Store   

     10th Most Common Venue  
0                Food Truck  
1               Bus Station  
2                Hobby Shop  
3                      Park  
4  Mediterranean Restaurant

In [50]:
scc_merged2

CITY    ZIP   LATITUDE   LONGITUDE  Cluster Labels0  \
0     SANTA CLARA  95050  37.355531 -121.955573                2   
1          GILROY  95020  37.004815 -121.572442                2   
2     MORGAN HILL  95037  37.125569 -121.662109                2   
3        CAMPBELL  95008  37.288126 -121.944362                2   
4        SAN JOSE  95113  37.337845 -121.886027                2   
5        MILPITAS  95035  37.432342 -121.897441                0   
6       SUNNYVALE  94086  37.371408 -122.036903                2   
7       LOS ALTOS  94022  37.381406 -122.113581                2   
8   MOUNTAIN VIEW  94039  37.390176 -122.081790                2   
9       PALO ALTO  94301  37.444255 -122.160528                1   
10      CUPERTINO  95014  37.318313 -122.028747                2   

    Average_Rent 1st Most Common Venue 2nd Most Common Venue  \
0           2974  Fast Food Restaurant   Fried Chicken Joint   
1           2215   American Restaurant    Mexican Restaurant   
2           2390        Ice Cream Shop         Grocery Store   
3           2633        Sandwich Place    Italian Restaurant   
4           2790        Sandwich Place        Ice Cream Shop   
5           2853        Shopping Plaza         Grocery Store   
6           3016         Grocery Store           Coffee Shop   
7           3060                Bakery           Coffee Shop   
8           3291           Coffee Shop                  Park   
9           3347                  Café        Ice Cream Shop   
10          3492                  Bank    Mexican Restaurant   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0       Indian Restaurant                  Bank                 Hotel   
1                    Café        Breakfast Spot                   Bar   
2       Convenience Store    Chinese Restaurant      Sushi Restaurant   
3      Mexican Restaurant           Pizza Place        Ice Cream Shop   
4   Vietnamese Restaurant    Mexican Restaurant           Coffee Shop   
5      Mexican Restaurant          Optical Shop        Sandwich Place   
6      Chinese Restaurant     Indian Restaurant                   Spa   
7        Sushi Restaurant    Mexican Restaurant           Pizza Place   
8             Yoga Studio                  Pool          Optical Shop   
9             Coffee Shop                 Hotel   American Restaurant   
10            Coffee Shop              Pharmacy    Chinese Restaurant   

   6th Most Common Venue    7th Most Common Venue 8th Most Common Venue  \
0         Breakfast Spot             Intersection            Art Museum   
1               Wine Bar                Bookstore     Indian Restaurant   
2            Pizza Place    Vietnamese Restaurant  Fast Food Restaurant   
3               Boutique       Frozen Yogurt Shop           Record Shop   
4      Convenience Store                      Pub              Pharmacy   
5     Chinese Restaurant                     Bank           Coffee Shop   
6                   Bank         Halal Restaurant   Rental Car Location   
7    American Restaurant                     Bank             Bookstore   
8       Sushi Restaurant  Health & Beauty Service    Salon / Barbershop   
9              Juice Bar     Gym / Fitness Center                   Spa   
10     Electronics Store           Sandwich Place        Mattress Store   

   9th Most Common Venue    10th Most Common Venue  
0     Italian Restaurant                Food Truck  
1            Coffee Shop               Bus Station  
2           Concert Hall                Hobby Shop  
3                 Arcade                      Park  
4            Music Store  Mediterranean Restaurant  
5     Seafood Restaurant        Salon / Barbershop  
6            Shoe Repair       Dumpling Restaurant  
7         Breakfast Spot          Greek Restaurant  
8            Salad Place               Pastry Shop  
9       Greek Restaurant               Pizza Place  
10        Massage Studio                       Spa

## Finally, let's visualize the resulting clusters

In [76]:
# create map
map_clusters2 = folium.Map(location=[37.354107, -121.955238], zoom_start=11)

map_clusters2.choropleth(geo_data=cities_santaclara,
                  data=Geo_scc_rental,
                  columns=['CITY', 'Average_Rent'],
                  key_on='feature.properties.name',
                  fill_color='YlOrRd', 
                  fill_opacity=0.7, 
                  line_opacity=0.2,
                  legend_name='Average rent by city'
)

# set color scheme for the clusters
x = np.arange(kclusters2)
ys = [i + x + (i*x)**2 for i in range(kclusters2)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(scc_merged2['LATITUDE'], scc_merged2['LONGITUDE'], scc_merged2['CITY'], scc_merged2['Cluster Labels0']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=10,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters2)
       
map_clusters2

In [52]:
scc_merged2.loc[scc_merged2['Cluster Labels0'] == 0, scc_merged2.columns[[1] + list(range(5, scc_merged2.shape[1]))]]

ZIP  Average_Rent 1st Most Common Venue 2nd Most Common Venue  \
5  95035          2853        Shopping Plaza         Grocery Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
5    Mexican Restaurant          Optical Shop        Sandwich Place   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
5    Chinese Restaurant                  Bank           Coffee Shop   

  9th Most Common Venue 10th Most Common Venue  
5    Seafood Restaurant     Salon / Barbershop

In [53]:
scc_merged2.loc[scc_merged2['Cluster Labels0'] == 1, scc_merged2.columns[[1] + list(range(5, scc_merged2.shape[1]))]]

ZIP  Average_Rent 1st Most Common Venue 2nd Most Common Venue  \
9  94301          3347                  Café        Ice Cream Shop   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
9           Coffee Shop                 Hotel   American Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
9             Juice Bar  Gym / Fitness Center                   Spa   

  9th Most Common Venue 10th Most Common Venue  
9      Greek Restaurant            Pizza Place

In [54]:
scc_merged2.loc[scc_merged2['Cluster Labels0'] == 2, scc_merged2.columns[[1] + list(range(5, scc_merged2.shape[1]))]]

ZIP  Average_Rent 1st Most Common Venue 2nd Most Common Venue  \
0   95050          2974  Fast Food Restaurant   Fried Chicken Joint   
1   95020          2215   American Restaurant    Mexican Restaurant   
2   95037          2390        Ice Cream Shop         Grocery Store   
3   95008          2633        Sandwich Place    Italian Restaurant   
4   95113          2790        Sandwich Place        Ice Cream Shop   
6   94086          3016         Grocery Store           Coffee Shop   
7   94022          3060                Bakery           Coffee Shop   
8   94039          3291           Coffee Shop                  Park   
10  95014          3492                  Bank    Mexican Restaurant   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0       Indian Restaurant                  Bank                 Hotel   
1                    Café        Breakfast Spot                   Bar   
2       Convenience Store    Chinese Restaurant      Sushi Restaurant   
3      Mexican Restaurant           Pizza Place        Ice Cream Shop   
4   Vietnamese Restaurant    Mexican Restaurant           Coffee Shop   
6      Chinese Restaurant     Indian Restaurant                   Spa   
7        Sushi Restaurant    Mexican Restaurant           Pizza Place   
8             Yoga Studio                  Pool          Optical Shop   
10            Coffee Shop              Pharmacy    Chinese Restaurant   

   6th Most Common Venue    7th Most Common Venue 8th Most Common Venue  \
0         Breakfast Spot             Intersection            Art Museum   
1               Wine Bar                Bookstore     Indian Restaurant   
2            Pizza Place    Vietnamese Restaurant  Fast Food Restaurant   
3               Boutique       Frozen Yogurt Shop           Record Shop   
4      Convenience Store                      Pub              Pharmacy   
6                   Bank         Halal Restaurant   Rental Car Location   
7    American Restaurant                     Bank             Bookstore   
8       Sushi Restaurant  Health & Beauty Service    Salon / Barbershop   
10     Electronics Store           Sandwich Place        Mattress Store   

   9th Most Common Venue    10th Most Common Venue  
0     Italian Restaurant                Food Truck  
1            Coffee Shop               Bus Station  
2           Concert Hall                Hobby Shop  
3                 Arcade                      Park  
4            Music Store  Mediterranean Restaurant  
6            Shoe Repair       Dumpling Restaurant  
7         Breakfast Spot          Greek Restaurant  
8            Salad Place               Pastry Shop  
10        Massage Studio                       Spa